# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper`.

You will find more info about virtual environments [here](../2.python/1.python_fundamentals/02.Package-Managers/00.Package_Managers.md).

Activate it.

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [15]:
# import the requests library (1 line)
import requests
# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = 'https://country-leaders.onrender.com'
# assign the /status endpoint to another variable called status_url (1 line)
status_url = root_url +'/status/'
# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(status_url)
# check the status_code using a condition and print appropriate messages (4 lines)
if req == 200:
    print("ok")
else:
    print("not found")


not found


### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [16]:
# Set the countries_url variable (1 line)
countries_url = root_url+'/countries'
# query the /countries endpoint using the get() method and store it in the req variable (1 line)
req =requests.get(countries_url)
# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()
# display the request's status code and the countries variable (1 line)
print(countries)

{'message': 'The cookie is missing'}


### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [17]:
# Set the cookie_url variable (1 line)
cookie_url = root_url+'/cookie'
# Query the enpoint, set the cookies variable and display it (2 lines)
r = requests.get(cookie_url)

print(f"{r.json()}")


{'message': 'The cookie has been created'}


Try to query the countries endpoint using the cookie, save the output and print it.

In [18]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries_url = root_url + '/countries'
countries = requests.get(countries_url,cookies = r.cookies)
print(f"{countries.json()}")

['us', 'be', 'fr', 'ma', 'ru']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [19]:
# Set the leaders_url variable (1 line)
leaders_url = root_url+"/leaders"
# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url,cookies = r.cookies)
# display the leaders variable (1 line)
print(f"{leaders.json()}")

{'message': 'Please specify a country'}


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [20]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)
leaders_url = root_url +"/leaders"
payload = {'country': 'us'}
# assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url,cookies = r.cookies,params=payload)
# display the leaders variable (1 line)
print(f"{leaders.json()}")

[{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'place_of_bi

### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each entry in a dictionary called `leaders_per_country` like this one: 
`{'fr':[{leader0}, {leader1},...],
'en':[{leader0}, {leader1},...],
...
}`.

In [21]:
# 4 lines
sourceFile = open('test.txt', 'w')
#cookie
cookie_url = root_url+'/cookie'
r = requests.get(cookie_url)

countries = countries.json()
leaders_per_country = {}

for countrie in countries:
    

    for leaders in countrie:
      params = {'country': countrie}
      leaders = requests.get(leaders_url,cookies = r.cookies,params=params)
      leaders = leaders.json()
      leaders_per_country[countrie] = leaders

print(leaders_per_country,file = sourceFile)
sourceFile.close()


It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [22]:
# < 15 lines
def get_leaders():
    root_url = 'https://country-leaders.onrender.com'
    cookie_url = root_url+'/cookie'
    leaders_url = root_url +"/leaders"
    countries_url = root_url + '/countries'

    r = requests.get(cookie_url)
    countries = requests.get(countries_url,cookies = r.cookies)
    countries = countries.json()
    leaders_per_country = {}
    for countrie in countries:
        for leaders in countrie:
            params = {'country': countrie} 
            leaders = requests.get(leaders_url,cookies = r.cookies,params=params)
            leaders = leaders.json()
            leaders_per_country[countrie] = leaders

    return leaders_per_country

    

Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [23]:
# 2 lines
leaders_per_country = get_leaders()
print(leaders_per_country)



{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [24]:
# 3 lines
leaders_per_country = get_leaders()

print(leaders_per_country['us'][2]['wikipedia_url'])
url_wiki = leaders_per_country['us'][0]['wikipedia_url']


https://en.wikipedia.org/wiki/Abraham_Lincoln


Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.


In [25]:
# 3 lines
from bs4 import BeautifulSoup

url_wiki = leaders_per_country['us'][0]['wikipedia_url']
wiki=requests.get(url_wiki)
wiki.text
html_wiki = BeautifulSoup(wiki.text, 'html.parser')
#print(soup.get_text())
print(html_wiki.prettify())



<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-language-alert-in-sidebar-enabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-enabled vector-feature-main-menu-pinned-disabled vector-feature-limited-width-enabled vector-feature-limited-width-content-enabled vector-feature-zebra-design-disabled" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   George Washington - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-language-alert-in-sidebar-enabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-enabled vector-feature-main-menu-pinned-disabled vector-feature-limited-width-enabled vector-feature-limited-width-conten

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [26]:
# 2 lines
paragraphs = [] 
for para in html_wiki.find_all("p"):
    paragraphs.append(para)
print(paragraphs)

[<p class="mw-empty-elt">
</p>, <p><b>George Washington</b> (February 22, 1732<sup class="reference" id="cite_ref-calendar_11-0"><a href="#cite_note-calendar-11">[b]</a></sup> – <span class="nowrap">December 14</span>, 1799) was an American military officer, statesman, and <a href="/wiki/Founding_Fathers_of_the_United_States" title="Founding Fathers of the United States">Founding Father</a> who served as the first <a href="/wiki/President_of_the_United_States" title="President of the United States">president of the United States</a> from 1789 to 1797. Appointed by the <a href="/wiki/Continental_Congress" title="Continental Congress">Continental Congress</a> as commander of the <a href="/wiki/Continental_Army" title="Continental Army">Continental Army</a>, Washington led <a href="/wiki/Patriot_(American_Revolution)" title="Patriot (American Revolution)">Patriot</a> forces to victory in the <a href="/wiki/American_Revolutionary_War" title="American Revolutionary War">American Revolutiona

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

In [33]:
# <10 lines

first_paragraph = ''
for paragraph in soup.find_all('p'):
    # if the paragraph contains bold text
    if paragraph.find('b'):
        # get the text
        first_paragraph = paragraph.get_text()
        # exit the loop
        break


NameError: name 'soup' is not defined

At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [34]:
# 10 lines
# def get_first_paragraph(wikipedia_url):
def get_first_paragraph(wikipedia_url):
#   print(wikipedia_url) # keep this for the rest of the notebook
    #print(wikipedia_url)
    wiki_text=requests.get(wikipedia_url).text
    soup = BeautifulSoup(wiki_text, 'html.parser')
    first_paragraph = ''
    for paragraph in soup.find_all('p'):
        if paragraph.find('b'):
            # get the text
            first_paragraph = paragraph.get_text()
            # exit the loop
            break
    #print(first_paragraph)
    return(first_paragraph)
#   return first_paragraph

In [35]:
# Test: 3 lines

get_first_paragraph('https://en.wikipedia.org/wiki/George_Washington')
get_first_paragraph('https://en.wikipedia.org/wiki/Barack_Obama')
get_first_paragraph('https://en.wikipedia.org/wiki/Abraham_Lincoln')




'Abraham Lincoln (/ˈlɪŋkən/ LINK-ən; February 12, 1809\xa0– April 15, 1865) was an American lawyer, politician, and statesman who served as the 16th president of the United States from 1861 until his assassination in 1865. Lincoln led the Union through the American Civil War to defend the nation as a constitutional union and succeeded in abolishing slavery, bolstering the federal government, and modernizing the U.S. economy.\n'

### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [30]:
# 3 lines
import re
text_to_clean = get_first_paragraph('https://en.wikipedia.org/wiki/Barack_Obama')
#re.sub(pattern, repl, string, count=0, flags=0)
re.sub(r" \(.*\)","",text_to_clean)


'Barack Hussein Obama II is an American politician who served as the 44th president of the United States from 2009 to 2017. A member of the Democratic Party, he was the first African-American  president of the United States.[2] Obama previously served as a U.S. senator representing Illinois from 2005 to 2008 and as an Illinois state senator from 1997 to 2004, and worked as a civil rights lawyer before holding public office. \n'

Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [31]:
# 10 lines
def get_first_paragraph(wikipedia_url):
#   print(wikipedia_url) # keep this for the rest of the notebook
    print(wikipedia_url)
    wiki_text=requests.get(wikipedia_url).text
    soup = BeautifulSoup(wiki_text, 'html.parser')
    first_paragraph = ''
    for paragraph in soup.find_all('p'):
        if paragraph.find('b'):
            # get the text
            first_paragraph = re.sub(r" \(.*\)","",paragraph.get_text())
            # exit the loop
            break
    print(first_paragraph)
    return(first_paragraph)
#   return first_paragraph


Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [32]:
# < 20 lines


## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [ ]:
# < 20 lines
def get_bio():
    root_url = 'https://country-leaders.onrender.com'
    cookie_url = root_url+'/cookie'
    leaders_url = root_url +"/leaders"
    countries_url = root_url + '/countries'

    r = requests.get(cookie_url)
    countries = requests.get(countries_url,cookies = r.cookies).json()
    leaders_per_country = {}
    for country in countries:
        
        params = {'country': country} 
        leaders_per_country[country] = requests.get(leaders_url, cookies = r.cookies, params=params).json()
        print(leaders_per_country[country])
        for leader in leaders_per_country[country]:
                leaders_per_country[country] = leader
                print(country)
                wiki_leader_url = leader["wikipedia_url"]
                get_first_paragraph(wiki_leader_url)
                leaders_per_country["bio"] = first_paragraph
    return leaders_per_country

In [ ]:
# Check the output of your function (2 lines)
get_bio()


Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [ ]:
# < 25 lines
def get_bio():
    root_url = 'https://country-leaders.onrender.com'
    cookie_url = root_url+'/cookie'
    leaders_url = root_url +"/leaders"
    countries_url = root_url + '/countries'

    r = requests.get(cookie_url)
    countries = requests.get(countries_url,cookies = r.cookies).json()
    leaders_per_country = {}
    for country in countries:
        status_url = root_url +'/status/'
        req = requests.get(status_url).status_code
        if req == 200:
            continue
        else:
           r = requests.get(cookie_url)
        params = {'country': country} 
        leaders_per_country[country] = requests.get(leaders_url, cookies = r.cookies, params=params).json()
        # print(leaders_per_country[country])
        for leader in leaders_per_country[country]:
            leaders_per_country[country] = leader
            wiki_leader_url = leader["wikipedia_url"]
            get_first_paragraph(wiki_leader_url)
            leaders_per_country["bio"] = first_paragraph
    return leaders_per_country


Check the output of your function again.

In [ ]:
# Check the output of your function (2 lines)
get_bio()

Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [ ]:
# < 20 lines
def get_first_paragraph(wikipedia_url,s):
#   print(wikipedia_url) # keep this for the rest of the notebook
    #print(wikipedia_url)
    wiki_text = s.get(wikipedia_url).text
    
    soup = BeautifulSoup(wiki_text, 'html.parser')
    first_paragraph = ''
    for paragraph in soup.find_all('p'):
        if paragraph.find('b'):
            # get the text
            first_paragraph = re.sub(r" \(.*\)","",paragraph.get_text())
            # exit the loop
            break
    return(first_paragraph)
#   return first_paragraph

Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [ ]:
# 25 lines
def get_leaders():
    root_url = 'https://country-leaders.onrender.com'
    cookie_url = root_url+'/cookie'
    leaders_url = root_url +'/leaders'
    countries_url = root_url + '/countries'

    s = requests.session()
    r = s.get(cookie_url)
    countries = s.get(countries_url,cookies = r.cookies).json()
    
    leaders_per_country = {}
    for country in countries:
        params = {'country': country} 
        req = s.get(leaders_url, cookies = r.cookies, params=params).status_code

        if req != 200:

            r = s.get(cookie_url)
            leaders = s.get(leaders_url, cookies = r.cookies, params=params).json()
            #print("cookie refresh")

        else:

            leaders = s.get(leaders_url, cookies = r.cookies, params=params).json()
            #print("cookie ok")
        leaders_per_country[country] = leaders
        for leader in leaders_per_country[country]:

            first_paragraph = get_first_paragraph(leader['wikipedia_url'], s)
            leader['bio'] = first_paragraph

    return leaders_per_country

: 

Test your new functions.



In [ ]:
# 2 lines
leaders_per_country = get_leaders()
print(leaders_per_country)

{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04', 'bio': 'George Washington was an American military officer, statesman, and Founding Father who served as the first president of the United States from 1789 to 1797. Appointed by the Continental Congress as commander of the Continental Army, Washington led Patriot forces to victory in the American Revolutionary War and served as president of the Constitutional Convention of 1787, which created and ratified the Constitution of the United States and the American federal government. Washington has been called the "Father of his Country" for his manifold leadership in the nation\'s founding.[10]\n'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date

## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [ ]:
# 3 lines
import json
with open( 'leaders.json','w' ) as outfile:
    json.dump(leaders_per_country,outfile)

<class 'list'>
[{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': Non

Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [ ]:
# 3 lines
with open( 'leaders.json','r' ) as outfile:
   data_leader_per_country= json.load(outfile)

# Check that the two dictionaries are identical.
if data_leader_per_country == leaders_per_country:
   print("dict are identical")
else:
   print("not good! work better!")

dict are identical


Make a function `save(leaders_per_country)` to call this code easily.

In [ ]:
# 3 lines
def save(leaders_per_country):
    import json
    with open( 'leaders.json','w' ) as outfile:
        json.dump(leaders_per_country,outfile,indent=4 )
    

In [ ]:
# Call the function (1 line)
save(leaders_per_country)

## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!

In [ ]:
s = requests.session()
r = s.get(cookie_url)
print(type(requests.get(leaders_url, cookies = r.cookies, params=params).json()))


<class 'list'>
